# Calculate utilities of two job decisions.


In [1]:
import pycop
import plotly.express as px
import numpy as np
from scipy import stats
import pyvinecopulib as pv

In [30]:
# https://realpython.com/python-super/#an-overview-of-pythons-super-function
class Pert(dist.Beta):
    """Class for modified-PERT distribution
    with parameters
    a: min
    b: mode
    c: max
    gamma: Lower values of gamma make for a
        distribution that is less peaked 
        at the mode.
    """
    def __init__(self, a, b, c, gamma=4):
        # https://pubsonline.informs.org/doi/epdf/10.1287/ited.1080.0013
        # Davis 2008 formula for conversion
        # between PERT and beta distributions
        # https://en.wikipedia.org/wiki/PERT_distribution#The_modified-PERT_distribution
        mu = (a + gamma * b + c)/(gamma + 2)
        # https://reference.wolfram.com/language/ref/PERTDistribution.html
        sigma_squared = (c - a - b*gamma + c*gamma)*(c + b*gamma - a * (1 + gamma))/((2 + gamma)**2 * (3 + gamma))
        alpha_plus_beta = (mu - a)*(c - mu)/sigma_squared - 1 
        alpha = (mu - a)/(c - a)*alpha_plus_beta
        beta = (c - mu)/(c - a)*alpha_plus_beta
        concentration1 = alpha
        concentration0 = beta
        super().__init__(concentration1, concentration0)

In [63]:
a = 69.5
b = 74
c = 76
gamma = 1
pert = Pert(a, b, c, gamma)
# https://num.pyro.ai/en/0.7.1/getting_started.html
y = a + pert.sample(key=rng_key, sample_shape=(100_000,))*(c - a)

In [62]:
fig = px.histogram(y)
fig.show()

Use vine copulas to work in high dimensions.
https://stats.stackexchange.com/a/580780/242887

In [8]:
# Specify pair-copulas
bicop = pv.Bicop(pv.BicopFamily.bb1, 90, [3, 2])
# https://vinecopulib.github.io/pyvinecopulib/_generate/pyvinecopulib.Vinecop.__init__.html
pair_copulas = [[bicop, bicop], [bicop]]

# Specify R-vine matrix
mat = np.array([[1, 1, 1], [2, 2, 0], [3, 0, 0]])

# Set-up a vine copula
cop = pv.Vinecop(
    matrix=mat, 
    pair_copulas=pair_copulas,
    var_types=["c", "d", "d"]
)
print(cop)

<pyvinecopulib.Vinecop>
** Tree: 0
3,1 <-> BB1 90°, parameters = 3
2
2,1 <-> BB1 90°, parameters = 3
2
** Tree: 1
3,2 | 1 <-> BB1 90°, parameters = 3
2



In [72]:
# https://en.wikipedia.org/wiki/Copula_(probability_theory)#Families_of_copulas
x, y, z = pycop.simulation.simu_archimedean(
    family="clayton",
    n=3,
    m=1000,
    theta=3
)

In [73]:
px.scatter(x=x, y=y)

In [64]:
px.scatter(x=y, y=z)

In [58]:
np.linalg.det(np.array([
        [1, 0.8, -0.6], 
        [0.8, 1, 0], 
        [-0.6, 0, 1]
    ]))

-5.32907051820077e-17

In [55]:
# Copula model of pay and probability of finding job
randoms_from_copula = pycop.simulation.simu_tstudent(
    n=2,
    m=1000,
    corr_matrix=np.array([
        [1, 0.8, -0.6], 
        [0.8, 1, 0], 
        [-0.6, 0, 1]
    ]),
    nu=1
)

LinAlgError: 3-th leading minor of the array is not positive definite

In [ ]:
# Copula model of pay and probability of finding job
randoms_from_copula = pycop.simulation.simu_archimedean(
    n=2,
    m=1000,
    corr_matrix=np.array([
        [1, 0.8, -0.6], 
        [0.8, 1, 0], 
        [-0.6, 0, 1]
    ]),
    nu=1
)

In [14]:
px.scatter(
    x=randoms_from_copula[0, :],
    y=randoms_from_copula[1, :]
)

In [16]:
px.histogram(randoms_from_copula[0, :])

In [21]:
u_1 = stats.beta.ppf(
    q=randoms_from_copula[0, :],
    a=2,
    b=3
)

u_2 = stats.beta.ppf(
    q=randoms_from_copula[1, :],
    a=2,
    b=30
)

In [23]:
np.corrcoef(u_1, u_2)

array([[1.        , 0.76164274],
       [0.76164274, 1.        ]])

In [24]:
np.corrcoef(randoms_from_copula[0, :], randoms_from_copula[1, :])

array([[1.       , 0.7639383],
       [0.7639383, 1.       ]])

# Calculate Utility of Decision A: Keep Current Employment for One More Year

Fixed Parameters:

- `personal_401k_contribution` = 0.05 (as a proportion of pay). This is for the next year.
- `employer_matching_401k_contribution` = 0 (as a proportion of `personal_401k_contribution`)
- `tier_2_employer_401k_contribution` = 0.14 (as a proportion of pay). See [this](https://www.urs.org/documents/byfilename/%7CPublic%20Web%20Documents%7CURS%7CDC%7C401k_SPD_SW%7C%7Capplication%7Cpdf/) for more information on 401(k) plans within the Utah Retirement System.
- `current_401k_transferrable_funds` = 2737.71
- `current_401k_nontransferrable_funds` = 18646.47
- `current_debt` = 5000
- `utility_of_3_day_weekend` = 100. This is the amount that one 3-day weekend is worth in dollars.
- `days_until_retirement` = 5*365

Random Variables:

- `initial_health_of_local_economy`: Given on a scale of 1-7. 1: Terrible. 2: Moderately poor. 3: Slightly poor. 4: Neither good nor bad. 5: Slightly good. 6: Moderately good. 7: Amazing.
- `health_of_local_economy_at_retirement`: Given on a scale of 1-7. 1: Terrible. 2: Moderately poor. 3: Slightly poor. 4: Neither good nor bad. 5: Slightly good. 6: Moderately good. 7: Amazing.
- `slope_of_health_of_local_economy = (health_of_local_economy_at_retirement - initial_health_of_local_economy) / days_until_retirement` 
- `health_of_local_economy = initial_health_of_local_economy + slope_of_health_of_local_economy * t` where `t` is the number of days since time zero.

- `initial_health_of_state_economy`: Given on a scale of 1-7. 1: Terrible. 2: Moderately poor. 3: Slightly poor. 4: Neither good nor bad. 5: Slightly good. 6: Moderately good. 7: Amazing.
- `health_of_state_economy_at_retirement`: Given on a scale of 1-7. 1: Terrible. 2: Moderately poor. 3: Slightly poor. 4: Neither good nor bad. 5: Slightly good. 6: Moderately good. 7: Amazing.
- `slope_of_health_of_state_economy = (health_of_state_economy_at_retirement - initial_health_of_state_economy) / days_until_retirement` 
- `health_of_state_economy = initial_health_of_state_economy + slope_of_health_of_state_economy * t` where `t` is the number of days since time zero.

- `initial_health_of_national_economy`: Given on a scale of 1-7. 1: Terrible. 2: Moderately poor. 3: Slightly poor. 4: Neither good nor bad. 5: Slightly good. 6: Moderately good. 7: Amazing.
- `health_of_national_economy_at_retirement`: Given on a scale of 1-7. 1: Terrible. 2: Moderately poor. 3: Slightly poor. 4: Neither good nor bad. 5: Slightly good. 6: Moderately good. 7: Amazing.
- `slope_of_health_of_national_economy = (health_of_national_economy_at_retirement - initial_health_of_national_economy) / days_until_retirement` 
- `health_of_national_economy = initial_health_of_national_economy + slope_of_health_of_national_economy * t` where `t` is the number of days since time zero.


5. `additional_days_employed_in_current_job`: Because this will be employment with a nice title, it will increase `prob_next_hire`.
6. `prob_next_hire`: probability of being hired after being laid off or reaching the year mark.
7. `days_until_next_hire`: If a layoff occurs, how many days would it take until you are hired for another job?
8. `annualized_ror_for_401k_transferrable_funds`: Annualized rate of return is calculated [here](https://en.wikipedia.org/wiki/Rate_of_return#Annualization). This will be used for the next year. 
9. `annualized_ror_for_401k_nontransferrable_funds`: This will be used for the next year.
10. `total_debt_payments_for_next_year`
11. `remaining_debt_at_end_of_year`
12. `days_until_debt_payoff`
13. `cucumulative_wages_earned_upon_retirement`: How much money was made from working since the decision was made to stay on the job?
14. `number_of_wage_changes`: How many times is your wage changed before the year is up or you are laid off?
15. `days_with_salary`: Random vector with length `number_of_wage_changes + 1`. The components represent the number of days between wage changes.

- `immediate_salary_change`: Categorical random variable with categories:

    0. salary changes to 0 (because of being laid off), 
    1. salary is decreased,
    2. salary stays the same,
    3. salary is increased

    It is called immediate because it is all about something happening within the year.
-  `probs_for_immediate_salary_change`: Dirichlet random vector with concentration parameters representing the probabilities of the categories for `immediate_salary_change`.




In [73]:
def stay_utility(
    rng_key,
    prob_laid_off_soon
):
    """Sample from the stochastic utility function

    for staying in the current job.

    Args:
        rng_key: 
        prob_laid_off_soon: probability of being laid off within the year

    Returns:  
    """
    # laid_off_current_job_soon is 1 if a layoff occurs in the next 
    # 12 months; otherwise, it is 0.
    laid_off_current_job_soon = dist.Bernoulli(prob_laid_off_soon)
    if laid_off_current_job_soon.sample(key=rng_key):
        # How many months of employment were
        # captured before the layoff?
        # arcsine distribution is Beta(0.5, 0.5)
        # https://en.wikipedia.org/wiki/Arcsine_distribution
        arcsine_dist = dist.Beta(0.5, 0.5)
        additional_months_employed_in_current_job = 12 * arcsine_dist.sample(key=rng_key)
    else:
        additional_months_employed_in_current_job = 12
    # pert_1 = Pert(a, b, c, gamma)
    # pert_2 = Pert(a, a + 0.1 * (c - a), c, 0.9*gamma)
    # # https://num.pyro.ai/en/0.7.1/getting_started.html
    # y = a + pert_1.sample(key=rng_key, sample_shape=(100_000,))*(c - a)
    # z = a + pert_2.sample(key=rng_key, sample_shape=(100_000,))*(c - a)

    # return y + z + z**3

In [98]:
copula = dist.GaussianCopulaBeta(np.array([2, 3]), np.array([4, 5]), np.array([[0.8]]))

In [99]:
copula.sample(key=rng_key)

ImportError: Please install `tensorflow_probability>=0.18` for betaincinv.

In [74]:
v = stay_utility(a=a, b=b, c=c, gamma=1.9, rng_key=rng_key)

In [75]:
fig = px.histogram(v)
fig.show()